# San Joaquin Valley Township Precipitation Data and Stations

Related links:

* For the documentation about this dataset, its source, how to download, and the features of interest, please refer to our [Well Completion Reports Dataset](/doc/assets/precipitation.md) documentation.
* For the explanations about the Public Land Survey System Township Range, please refer to our [Public Land Survey System](../assets/plss_sanjoaquin_riverbasin.md) documentation.
* For the explanations on how we transform point measurements of precipitation by weather stations into township precipitation estimates, please refer to our [Transforming Point Values into Township Values](doc/etl/from_point_to_region_values.md) documentation.


In [1]:
import sys
sys.path.append('..')

In [2]:
import matplotlib.pyplot as plt
import altair as alt
from lib.precipitation_v2 import PrecipitationDataset
from lib.viz import view_year_side_by_side, display_data_on_map, simple_geodata_viz

In [3]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

By initializing the PrecipitationDataset class, it automatically:
* scraps the web to retrieve the precipitation data for the state of California (default is between 2013 and 2022)
* scraps the web to retrieve the geospatial data of the precipitation stations in California

In [4]:
precipitation_dataset = PrecipitationDataset()

Here is an overview of the monthly precipitation data scrapped from the web.

In [5]:
precipitation_dataset.data_df

STATION_ID              STATION_NAME  AVERAGE_YEARLY_PRECIPITATION  YEAR
0           ALT                ALTURAS RS                      0.842500  2013
1           APU  ANGWIN PACIFIC UNION COL                      3.312000  2013
2           ASM              ASH MOUNTAIN                      1.281667  2013
3           ATW               ATWELL CAMP                      2.128333  2013
4           ABR              AUBERRY 2 NW                      1.635000  2013
...         ...                       ...                           ...   ...
1762        WVR            WEAVERVILLE RS                      3.830000  2022
1763        WPT                WEST POINT                      6.287500  2022
1764        WDL            WOODLAND 1 WNW                      3.055000  2022
1765        YSV     YOSEMITE HEADQUARTERS                      5.312500  2022
1766        YRK                     YREKA                      2.177500  2022

[1767 rows x 4 columns]

By default the precipitation data are collected for the following years:

In [6]:
list(precipitation_dataset.data_df.YEAR.unique())

[2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020, 2021, 2022]

Here is an overview of the precipitation stations geospatial data scrapped from the web.

In [7]:
precipitation_dataset.map_df

STATION STATION_ID ELEV(FEET)   LATITUDE  \
0         DWINNELL RESERVOIR NEAR EDGEWOOD        DRE       2805  41.540894   
1                             TRINITY LAKE        CLE       2370  40.800999   
2                                 LEWISTON        LEW       1870  40.727001   
3                                RUTH  DAM        RTD       2675  40.367001   
4    LAKE PILLSBURY NR POTTER VLY 24HR AVG        LPY       1828  39.408298   
..                                     ...        ...        ...        ...   
201                     TINEMAHA RESERVOIR        TNM       3882  37.057999   
202                                 HAIWEE        HWE       3774  36.137001   
203                   SOUTH LAKE RESERVOIR        SKR        837  33.115040   
204                  LITTLE ROCK RESERVOIR        LRK        745  34.485001   
205                        LAKE SILVERWOOD        SLW       3331  34.304001   

       LONGITUDE          COUNTY                     geometry  
0    -122.374550        SISKIYOU  POINT (-122.37455 41.54089)  
1    -122.762001         TRINITY  POINT (-122.76200 40.80100)  
2    -122.792999         TRINITY  POINT (-122.79300 40.72700)  
3    -123.432999         TRINITY  POINT (-123.43300 40.36700)  
4    -122.958298            LAKE  POINT (-122.95830 39.40830)  
..           ...             ...                          ...  
201  -118.224998            INYO  POINT (-118.22500 37.05800)  
202  -117.947998            INYO  POINT (-117.94800 36.13700)  
203  -117.165588            INYO  POINT (-117.16559 33.11504)  
204  -118.022003     LOS ANGELES  POINT (-118.02200 34.48500)  
205  -117.318001  SAN BERNARDINO  POINT (-117.31800 34.30400)  

[206 rows x 7 columns]

In [8]:
precipitation_dataset.preprocess_map_df(features_to_keep=["STATION_ID", "COUNTY", "geometry"])
precipitation_dataset.merge_map_with_data(how="inner", dropkeys=True, dropna=True)
precipitation_dataset.map_df

COUNTY                     geometry          STATION_NAME  \
0    SANTA BARBARA  POINT (-119.98000 34.58300)          CACHUMA LAKE   
1    SANTA BARBARA  POINT (-119.98000 34.58300)          CACHUMA LAKE   
2    SANTA BARBARA  POINT (-119.98000 34.58300)          CACHUMA LAKE   
3    SANTA BARBARA  POINT (-119.98000 34.58300)          CACHUMA LAKE   
4    SANTA BARBARA  POINT (-119.98000 34.58300)          CACHUMA LAKE   
..             ...                          ...                   ...   
137           INYO  POINT (-117.94800 36.13700)                HAIWEE   
138           INYO  POINT (-117.94800 36.13700)                HAIWEE   
139           INYO  POINT (-117.94800 36.13700)                HAIWEE   
140           INYO  POINT (-117.94800 36.13700)                HAIWEE   
141           INYO  POINT (-117.16559 33.11504)  SOUTH LAKE RESERVOIR   

     AVERAGE_YEARLY_PRECIPITATION  YEAR  
0                        0.632500  2013  
1                        0.829167  2014  
2                        1.330909  2015  
3                        0.954167  2016  
4                        2.123333  2017  
..                            ...   ...  
137                      0.892500  2019  
138                      0.679167  2020  
139                      0.108333  2021  
140                      0.380000  2022  
141                      1.910000  2022  

[142 rows x 5 columns]

Let's look at California's precipitation recording station locations compared to the San Joaquin Valley townships for the year 2021

In [9]:
display_data_on_map(precipitation_dataset.map_df, feature="AVERAGE_YEARLY_PRECIPITATION", year=2021)

Next, based on the precipitation station points, we compute Voronoi Diagram with the Thiessen Polygon for each station

In [10]:
precipitation_dataset.compute_areas_from_points()

In [12]:
simple_geodata_viz(precipitation_dataset.map_df, feature="AVERAGE_YEARLY_PRECIPITATION", title="Area mesutements from weather stations", year=2021, draw_stations=True)

alt.LayerChart(...)

Then we clip the data to the San Joaquin Valley boundaries and overlay the Township boundaries

In [13]:
precipitation_dataset.overlay_township_boundries()
precipitation_dataset.map_df

COUNTY         STATION_NAME  AVERAGE_YEARLY_PRECIPITATION  YEAR  \
0              KERN         ISABELLA DAM                      0.829167  2018   
1              KERN         ISABELLA DAM                      0.829167  2018   
2              KERN         ISABELLA DAM                      0.829167  2018   
3              KERN         ISABELLA DAM                      0.829167  2018   
4     SANTA BARBARA         CACHUMA LAKE                      0.776667  2018   
...             ...                  ...                           ...   ...   
5645         NEVADA  ENGLEBRIGHT (USACE)                      5.060000  2022   
5646         NEVADA  ENGLEBRIGHT (USACE)                      5.060000  2022   
5647         NEVADA  ENGLEBRIGHT (USACE)                      5.060000  2022   
5648         NEVADA  ENGLEBRIGHT (USACE)                      5.060000  2022   
5649         TULARE          SUCCESS DAM                      1.680000  2022   

                           points TOWNSHIP_RANGE  \
0     POINT (-118.47300 35.64600)      T10N R18W   
1     POINT (-118.47300 35.64600)      T10N R19W   
2     POINT (-118.47300 35.64600)      T10N R20W   
3     POINT (-118.47300 35.64600)      T10N R21W   
4     POINT (-119.98000 34.58300)      T10N R21W   
...                           ...            ...   
5645  POINT (-121.26700 39.23900)      T07N R07E   
5646  POINT (-121.26700 39.23900)      T07N R08E   
5647  POINT (-121.26700 39.23900)      T07N R09E   
5648  POINT (-121.26700 39.23900)      T08N R08E   
5649  POINT (-118.92200 36.06100)            NaN   

                                               geometry  
0     POLYGON ((-118.75899 34.92296, -118.84692 34.9...  
1     POLYGON ((-118.84692 34.89763, -118.95383 34.8...  
2     POLYGON ((-119.06489 34.91157, -119.06489 34.9...  
3     POLYGON ((-119.08916 34.91979, -119.13910 34.9...  
4     POLYGON ((-119.08916 34.91979, -119.17084 34.9...  
...                                                 ...  
5645  POLYGON ((-121.26066 38.49634, -121.14953 38.4...  
5646  POLYGON ((-121.07591 38.49584, -121.03868 38.4...  
5647  POLYGON ((-120.98258 38.49929, -120.98258 38.4...  
5648  POLYGON ((-121.07591 38.51033, -121.03862 38.5...  
5649  MULTIPOLYGON (((-119.96822 35.96414, -119.9682...  

[5650 rows x 7 columns]

In [14]:
simple_geodata_viz(precipitation_dataset.map_df, feature="AVERAGE_YEARLY_PRECIPITATION", title="San Joaquin Valley Township-Ranges precipitation measurement areas", year=2021, draw_stations=True)

alt.LayerChart(...)

Because of the way we [transform point measurements of precipitation by weather stations into township precipitation estimates](doc/etl/from_point_to_region_values.md), although there are 16 weather stations in the San Joaquin Valley, a total of 33 stations are use to estimate the county-townships precipitations. Looking at their value average yearly precipitation measurement per year, we get.

In [15]:
station_precipitation_per_year_df = precipitation_dataset.map_df[["YEAR", "AVERAGE_YEARLY_PRECIPITATION", "STATION_NAME"]].drop_duplicates()
alt.Chart(station_precipitation_per_year_df).mark_bar().encode( x="YEAR:N",y='AVERAGE_YEARLY_PRECIPITATION:Q', color='STATION_NAME:N')

alt.Chart(...)

We then compute the precipitation value at the Township level. As some townships cross several Voronoïd areas, for every year, for every Township we take the mean of the values of the Voronoïd areas crossing that Township.

In [16]:
precipitation_dataset.aggregate_areas_within_townships(group_by_features=["TOWNSHIP_RANGE", "YEAR"])
precipitation_dataset.map_df

TOWNSHIP_RANGE  YEAR                                           geometry  \
0         T01N R02E  2013  POLYGON ((-121.78743 37.88191, -121.78743 37.9...   
1         T01N R02E  2014  POLYGON ((-121.78743 37.88191, -121.78743 37.9...   
2         T01N R02E  2015  POLYGON ((-121.78743 37.88191, -121.78743 37.9...   
3         T01N R02E  2016  POLYGON ((-121.78743 37.88191, -121.78743 37.9...   
4         T01N R02E  2017  POLYGON ((-121.78743 37.88191, -121.78743 37.9...   
...             ...   ...                                                ...   
4775      T32S R30E  2018  POLYGON ((-118.73539 35.09396, -118.73539 35.0...   
4776      T32S R30E  2019  POLYGON ((-118.73539 35.09396, -118.73539 35.0...   
4777      T32S R30E  2020  POLYGON ((-118.73539 35.09396, -118.73539 35.0...   
4778      T32S R30E  2021  POLYGON ((-118.73539 35.09396, -118.73539 35.0...   
4779      T32S R30E  2022  POLYGON ((-118.73539 35.09396, -118.73539 35.0...   

      AVERAGE_YEARLY_PRECIPITATION  
0                         2.845833  
1                         1.664167  
2                         2.019167  
3                         3.025000  
4                         4.992500  
...                            ...  
4775                      0.829167  
4776                      2.169167  
4777                      0.994167  
4778                      0.421667  
4779                      2.210000  

[4780 rows x 4 columns]

In [17]:
view_year_side_by_side(precipitation_dataset.map_df, feature="AVERAGE_YEARLY_PRECIPITATION", title="San Joaquin Valley average yearly precipitation estimates")

alt.ConcatChart(...)

The dataset is ready for output

In [18]:
precipitation_dataset.prepare_output_from_map_df()
precipitation_dataset.output_dataset_to_csv("../assets/outputs/precipitations.csv")
precipitation_dataset.output_df

TOWNSHIP_RANGE  YEAR  AVERAGE_YEARLY_PRECIPITATION
0         T01N R02E  2013                      2.845833
1         T01N R02E  2014                      1.664167
2         T01N R02E  2015                      2.019167
3         T01N R02E  2016                      3.025000
4         T01N R02E  2017                      4.992500
...             ...   ...                           ...
4775      T32S R30E  2018                      0.829167
4776      T32S R30E  2019                      2.169167
4777      T32S R30E  2020                      0.994167
4778      T32S R30E  2021                      0.421667
4779      T32S R30E  2022                      2.210000

[4780 rows x 3 columns]